# Tool Calling

The IONOS AI Model Hub offers tool calling as a feature of our OpenAI-compatible text generation API. Tool calling allows the Large Language Model (LLM) to integrate other tools and APIs into the conversation. This helps 
extending the functionality of Large Language Models beyond the pretrained data and data in vector databases.

**Note:** The older term "function calling" is now deprecated in favor of "tool calling" in modern AI APIs. This tutorial uses the current standard terminology.

## Text Generation Models Supporting Tool Calling

Only the following Large Language Models offer tool calling:

| Model Provider | Model Name | Purpose |
|-----------------------------------------|---------------------------|---------------------------------------------------------------------------------------------------------------------------------------------------------------------|
| Meta ([<mark style="color:blue;">**License**</mark>](https://llama.meta.com/llama3_3/license/)) | Llama 3.3 Instruct (70B) | Ideal for dialogue use cases and natural language tasks: conversational agents, virtual assistants, and chatbots. Exceeds the performance of Llama 3.1 405B at comparably quality levels.| 
| Meta ([<mark style="color:blue;">**License**</mark>](https://llama.meta.com/llama3/license/)) | Llama 3.1 Instruct (8B and 405B) | Ideal for dialogue use cases and natural language tasks: conversational agents, virtual assistants, and chatbots. | 
| Mistral AI ([<mark style="color:blue;">**License**</mark>](https://www.apache.org/licenses/LICENSE-2.0.html)) | Mistral Instruct v0.3 (7B) | Ideal for: Conversational agents, virtual assistants, and chatbots; Comparison to Llama 3: better with European languages; supports longer context length.|

**Unsuported models:** Although we offer Teuken and Mixtral 8x7B as foundation models, these models do not support
tool calling.

## Overview

In this tutorial, you will learn how to integrate tool calling into a Large Language Model via the OpenAI 
compatible API to generate a weather forecast. This tutorial is intended for developers with basic knowledge of:
- REST APIs
- A programming language for handling REST API endpoints (Python and Bash examples are provided)
- Applying Large Language Models using our OpenAI compatbile ([<mark style="color:blue;">**text generation**</mark>](../text-generation/README.md)) enpoint.

By the end, you will be able to:
1\. Define tool schemas that describe available external tools
2\. Process user queries to determine when to call these tools
3\. Handle tool responses to provide meaningful answers to users

## Getting Started with Tool Calling

To use tool calling, first set up your environment and authenticate using the OpenAI-compatible API endpoints.

Download the respective code files to easily access tool calling-specific scripts and examples and generate the intended output:

### Prerequisite: Access API Token from Environment Variable

We strongly suggest that you save your IONOS API token as environment variable in your operating system. You can then access it using the following lines of code:

In [1]:
from dotenv import load_dotenv
import os

load_dotenv()
IONOS_API_TOKEN = os.getenv('IONOS_API_TOKEN')

### Step 1: Retrieve Available Models

Fetch a list of models to see which are available for your use case:

In [2]:
import requests

endpoint = "https://openai.inference.de-txl.ionos.com/v1/models"

header = {
    "Authorization": f"Bearer {IONOS_API_TOKEN}", 
    "Content-Type": "application/json"
}
requests.get(endpoint, headers=header).json()

{'data': [{'id': 'meta-llama/Meta-Llama-3.1-405B-Instruct-FP8',
   'object': 'model',
   'created': 1677610602,
   'owned_by': 'openai'},
  {'id': 'BAAI/bge-large-en-v1.5',
   'object': 'model',
   'created': 1677610602,
   'owned_by': 'openai'},
  {'id': 'stabilityai/stable-diffusion-xl-base-1.0',
   'object': 'model',
   'created': 1677610602,
   'owned_by': 'openai'},
  {'id': 'BAAI/bge-m3',
   'object': 'model',
   'created': 1677610602,
   'owned_by': 'openai'},
  {'id': 'meta-llama/Llama-3.3-70B-Instruct',
   'object': 'model',
   'created': 1677610602,
   'owned_by': 'openai'},
  {'id': 'black-forest-labs/FLUX.1-schnell',
   'object': 'model',
   'created': 1677610602,
   'owned_by': 'openai'},
  {'id': 'meta-llama/Meta-Llama-3.1-8B-Instruct',
   'object': 'model',
   'created': 1677610602,
   'owned_by': 'openai'},
  {'id': 'sentence-transformers/paraphrase-multilingual-mpnet-base-v2',
   'object': 'model',
   'created': 1677610602,
   'owned_by': 'openai'},
  {'id': 'openGPT-X

This query returns a JSON document listing each models name, which you’ll use to specify a model for text generation in later steps.

### Step 2: Define your Functions

To start integrating functions into you your project, you first need to implement these functions. These functions
could be any type of functions in your existing code, they could be API endpoints or anything similar.

As a running example, we assume, that we want to integrate one function which returns weather data:

In [3]:
def get_weather(city: str, unit: str="celsius"):
    """Get the current weather in a given location"""
    # In a real implementation, this would call a weather API
    # This is a mock implementation
    if city.lower() == "berlin":
        temperature = 22 if unit == "celsius" else 72
        weather_data = {
            "city": city,
            "temperature": temperature,
            "unit": unit,
            "forecast": ["sunny", "windy"],
            "humidity": 70
        }
        return weather_data
    return {"error": "Location not supported"}

### Step 3: Derive Tool Definition

Given the function 'get_weather' implemented in **Step 1**, one can derive the tool definition:

In [4]:
tools = [
    {
        "type": "function",
        "function": {
            "name": "get_weather",
            "description": "Get the current weather in a given city",
            "parameters": {
                "type": "object",
                "properties": {
                    "city": {
                        "type": "string",
                        "description": "The city for which the weather should be returned"
                    },
                    "unit": {
                        "type": "string",
                        "enum": ["celsius", "fahrenheit"],
                        "description": "The unit of temperature to use. Is inferred from the city if possible."
                    }
                },
                "required": ["city", "unit"]
            }
        }
    }
]

### Step 4: Enrich User Query with Available Tool Definitions

You can now invoke a user query and specify the tool definitions during invocation:

In [5]:
import requests
import json
from openai import OpenAI

MODEL_NAME = "meta-llama/Llama-3.3-70B-Instruct"
IONOS_API_URL = 'https://openai.inference.de-txl.ionos.com/v1'

# Initialize the OpenAI client with IONOS API URL
client = OpenAI(base_url=IONOS_API_URL, api_key=IONOS_API_TOKEN)

user_query = "What's the weather like in Berlin?"

body = {
    "model": MODEL_NAME,
    "messages": [
        {"role": "user", "content": user_query}
    ],
    "tools": tools,
    "tool_choice": "auto"  # Let the model decide when to call tools
}

response = client.chat.completions.create(**body)
response

ChatCompletion(id='chatcmpl-6e642b8426464db0a80879ae60248ca0', choices=[Choice(finish_reason='tool_calls', index=0, logprobs=None, message=ChatCompletionMessage(content=None, refusal=None, role='assistant', annotations=None, audio=None, function_call=None, tool_calls=[ChatCompletionMessageToolCall(id='chatcmpl-tool-05b7cd0752d04098b6ea91f3c8fcc328', function=Function(arguments='{"city": "Berlin", "unit": "celsius"}', name='get_weather'), type='function')]))], created=1742395027, model='meta-llama/Llama-3.3-70B-Instruct', object='chat.completion', service_tier=None, system_fingerprint=None, usage=CompletionUsage(completion_tokens=30, prompt_tokens=318, total_tokens=348, completion_tokens_details=None, prompt_tokens_details=None), prompt_logprobs=None)

### Step 5: Process the Tool Call Response and Execute Tool

The Large Language Modell will very likely recognize that the query requires weather data and will respond with a 
**tool call**. We need to parse this **tool call** that needs to be parsed:

In [6]:
# Parse tool call and arguments
if response.choices[0].message.tool_calls:
    tool_call = response.choices[0].message.tool_calls[0]
    function_name = tool_call.function.name
    function_args = json.loads(tool_call.function.arguments)
    
    # Call the function
    if function_name == "get_weather":
        tool_response = get_weather(
            city=function_args.get("city"),
            unit=function_args.get("unit")
        )
    print(tool_response)
else:
    print("The model provided a direct response (no tool call):")
    print(response['choices'][0]['message']['content'])

{'city': 'Berlin', 'temperature': 22, 'unit': 'celsius', 'forecast': ['sunny', 'windy'], 'humidity': 70}


## Summary

In this tutorial, you learned how to:
1. Create a mock weather data function that simulates a real API
2. Define a tool definition based on the weather data function
3. Process user queries to determine when to call the weather data function
4. Parse the Large Language Model response and use it to invoke the weather data function

Tool calling opens up numerous possibilities for creating more capable AI applications that can interact with external
systems and provide real-time data to users.

For more information on other API capabilities, refer to our documentation on [<mark style="color:blue;">text generation</mark>](https://docs.ionos.com/cloud/ai/ai-model-hub/how-tos/text-generation/README.md) and [<mark style="color:blue;">image generation</mark>](https://docs.ionos.com/cloud/ai/ai-model-hub/how-tos/image-generation/README.md) models.